In [2]:
import torch
import torch.nn as nn
import torch.optim as optim
from torchvision import datasets, transforms
from torch.utils.data import DataLoader, Subset,TensorDataset
from autoencoder2 import Autoencoder2, reduce_dimensions2
import torchvision
from model2 import classification_model
import copy
import partition
from pca import PCADigitReducer
from training import train,test, train_fashion,test_fashion
from federated_learning import distribute_global_model, federated_averaging
from model4 import MultilayerPerceptron
import cluster2
from sklearn.metrics import precision_score, recall_score, f1_score
import time

# Preprocessing

In [3]:
n_epochs = 10
batch_size_train = 64
batch_size_test = 1000
learning_rate = 0.01 # ev. 0.001
momentum = 0.5
log_interval = 10

random_seed = 1
torch.backends.cudnn.enabled = False
torch.manual_seed(random_seed)

In [4]:
transform = transforms.Compose([
    transforms.ToTensor(),
    transforms.Normalize((0.0,), (1.0,))
])


train_dataset = torchvision.datasets.KMNIST(root='./data', train=True, download=True, transform=transform)
test_dataset = torchvision.datasets.KMNIST(root='./data', train=False, download=True, transform=transform)


kanji_train_loader = torch.utils.data.DataLoader(train_dataset, batch_size=64, shuffle=True)
kanji_test_loader = torch.utils.data.DataLoader(test_dataset, batch_size=64, shuffle=False)

In [5]:
train_loader_pca = copy.copy(kanji_train_loader)
test_loader_pca = copy.copy(kanji_test_loader)

train_loader_auto = copy.copy(kanji_train_loader)
test_loader_auto = copy.copy(kanji_test_loader)

In [6]:
class CustomTensorDataset(TensorDataset):
    def __init__(self, *tensors):
        super().__init__(*tensors)
        self.data = tensors[0]
        self.targets = tensors[1] 

# PCA

# Autoencoder

In [7]:
# Autoencoder
#latent_dim = 100  
autoencoder = Autoencoder2()
auto_criterion = nn.MSELoss()
auto_optimizer = optim.Adam(autoencoder.parameters(), lr=1e-3)
auto_num_epochs = 5
for epoch in range(auto_num_epochs): 
    for images, _ in train_loader_auto:
        auto_optimizer.zero_grad()
        reconstructed = autoencoder(images)
        loss = auto_criterion(reconstructed, images)  
        loss.backward()
        auto_optimizer.step()
        
    print(f"Epoch [{epoch+1}/5], Loss: {loss.item()}")

Epoch [1/5], Loss: 0.02510267123579979
Epoch [2/5], Loss: 0.019388481974601746
Epoch [3/5], Loss: 0.01728295162320137
Epoch [4/5], Loss: 0.015834297984838486
Epoch [5/5], Loss: 0.013073240406811237


# Experiment

In [10]:
alpha = 0.5
num_clients = 10
num_clusters = [2, 4, 6, 8, 10]
results = {"classic": {}, "pca": {}, "autoencoder": {}}
clusteredResults = {"classic": {}, "pca": {}, "autoencoder": {}}

# Classic

In [11]:
trainingset = kanji_train_loader.dataset
trial_model_strong = MultilayerPerceptron()
global_model_classic_strong = MultilayerPerceptron()
rounds_classic = 8

In [9]:

partitioned_data_classic = partition.balanced_dirichlet_partition(
    trainingset, partitions_number=num_clients, alpha=alpha)

classic_client_loaders = [
    DataLoader(Subset(trainingset, indices), batch_size=batch_size_train, shuffle=True)
    for indices in partitioned_data_classic.values()
]

local_models_classic_strong = [copy.deepcopy(global_model_classic_strong) for _ in range(num_clients)]


for round_idx in range(rounds_classic):
    print(f"Round {round_idx + 1}/{rounds_classic}")
    t1=time.time()

    local_weights_classic = []
    for client_idx, client_model in enumerate(local_models_classic_strong):
        print(f"Training client {client_idx + 1}")
        
        optimizer = optim.SGD(client_model.parameters(), lr=learning_rate,
                      momentum=momentum)

        train_losses = []
        train_counter = []

        for epoch in range(1, n_epochs + 1):  
            train_fashion(epoch, client_model, classic_client_loaders[client_idx], optimizer, log_interval, train_losses, train_counter)
        
        client_weights = [param.data.numpy() for param in client_model.parameters()]
        local_weights_classic.append(client_weights)
        

    global_weights_classic = federated_averaging(local_weights_classic)


    distribute_global_model(global_weights_classic,local_models_classic_strong,single=False)

    distribute_global_model(global_weights_classic,global_model_classic_strong,single=True)
    test_losses = []
    test_fashion(global_model_classic_strong,kanji_test_loader,test_losses)
    t2= time.time()


    test_accuracies_classic = []
    correct = 0
    all_preds = []
    all_targets = []
    with torch.no_grad():
        for data, target in kanji_test_loader:
            data = data.view(data.shape[0], -1)
            output = global_model_classic_strong(data)
            pred = output.data.max(1, keepdim=True)[1]
            all_preds.extend(pred.cpu().numpy().flatten())
            all_targets.extend(target.cpu().numpy().flatten())
            correct += pred.eq(target.data.view_as(pred)).sum().item()

    accuracy = 100. * correct / len(kanji_test_loader.dataset)
    test_accuracies_classic.append(accuracy)
    precision = precision_score(all_targets, all_preds, average='macro')
    recall = recall_score(all_targets, all_preds, average='macro')
    f1 = f1_score(all_targets, all_preds, average='macro')


    results["classic"]["NoCluster"] = {"losses": [], "accuracy": [], "precision": [], "recall": [], "f1": [], "trainingTime": []}

    results["classic"]["NoCluster"]["losses"].extend(test_losses)
    results["classic"]["NoCluster"]["accuracy"].extend(test_accuracies_classic)
    results["classic"]["NoCluster"]["precision"].append(precision)
    results["classic"]["NoCluster"]["recall"].append(recall)
    results["classic"]["NoCluster"]["f1"].append(f1)
    results["classic"]["NoCluster"]["trainingTime"].append(t2-t1)

    ######################
for num_cluster in num_clusters:
    import cluster2

    targets = trainingset.targets
    num_classes = len(set(targets)) 
    clients = [cluster2.FederatedClient(cid, indices, targets, num_classes) for cid, indices in partitioned_data_classic.items()]
    client_distributions = [client.compute_label_distribution() for client in clients]
    server = cluster2.FederatedClusterServer(num_cluster)
    aggregated_data = server.aggregate_client_data(client_distributions)
    clustered_data = server.perform_greedy_clustering(aggregated_data, partitioned_data_classic)
    
    partitioned_data_classic_clustered = clustered_data

    """
    import cluster
    cluster = cluster.Cluster(num_clusters=num_cluster)
    
    targets = trainingset.targets
    num_classes = len(set(targets)) 
    clustered_data = cluster.apply_clustering(partitioned_data_classic, targets, num_classes)
    
    partitioned_data_classic_clustered = clustered_data
    """

    classic_client_loaders_clustered = [
        DataLoader(Subset(trainingset, indices), batch_size=batch_size_train, shuffle=True)
        for indices in partitioned_data_classic_clustered.values()
    ]

    for round_idx in range(rounds_classic):
        print(f"Round {round_idx + 1}/{rounds_classic}")
        t1=time.time()

        local_weights_classic = []
        for client_idx, client_model in enumerate(local_models_classic_strong[0:num_cluster]):
            print(f"Training client {client_idx + 1}")
            
            optimizer = optim.SGD(client_model.parameters(), lr=learning_rate,
                          momentum=momentum)
    
            train_losses = []
            train_counter = []
    
            for epoch in range(1, n_epochs + 1):  
                train_fashion(epoch, client_model, classic_client_loaders[client_idx], optimizer, log_interval, train_losses, train_counter)
            
            client_weights = [param.data.numpy() for param in client_model.parameters()]
            local_weights_classic.append(client_weights)
            
    
        global_weights_classic = federated_averaging(local_weights_classic)
    
    
        distribute_global_model(global_weights_classic,local_models_classic_strong,single=False)
    
        distribute_global_model(global_weights_classic,global_model_classic_strong,single=True)
        test_losses = []
        test_fashion(global_model_classic_strong,kanji_test_loader,test_losses)
        t2= time.time()

        test_accuracies_classic = []
        correct = 0
        all_preds = []
        all_targets = []
        with torch.no_grad():
            for data, target in kanji_test_loader:
                data = data.view(data.shape[0], -1)
                output = global_model_classic_strong(data)
                pred = output.data.max(1, keepdim=True)[1]
                all_preds.extend(pred.cpu().numpy().flatten())
                all_targets.extend(target.cpu().numpy().flatten())
                correct += pred.eq(target.data.view_as(pred)).sum().item()

        accuracy = 100. * correct / len(kanji_test_loader.dataset)
        test_accuracies_classic.append(accuracy)
        precision = precision_score(all_targets, all_preds, average='macro')
        recall = recall_score(all_targets, all_preds, average='macro')
        f1 = f1_score(all_targets, all_preds, average='macro')

        if num_cluster not in clusteredResults["classic"]:
            clusteredResults["classic"][num_cluster] = {"losses": [], "accuracy": [], "precision": [], "recall": [], "f1": [], "trainingTime": []}

        clusteredResults["classic"][num_cluster]["losses"].extend(test_losses)
        clusteredResults["classic"][num_cluster]["accuracy"].extend(test_accuracies_classic)
        clusteredResults["classic"][num_cluster]["precision"].append(precision)
        clusteredResults["classic"][num_cluster]["recall"].append(recall)
        clusteredResults["classic"][num_cluster]["f1"].append(f1)
        clusteredResults["classic"][num_cluster]["trainingTime"].append(t2-t1)

Round 1/8
Training client 1
Train Epoch: 1 [0/2540 (0%)]	Loss: 2.308557
Train Epoch: 1 [640/2540 (25%)]	Loss: 2.258530
Train Epoch: 1 [1280/2540 (50%)]	Loss: 2.185721
Train Epoch: 1 [1920/2540 (75%)]	Loss: 2.055395
Train Epoch: 2 [0/2540 (0%)]	Loss: 1.946211
Train Epoch: 2 [640/2540 (25%)]	Loss: 1.947338
Train Epoch: 2 [1280/2540 (50%)]	Loss: 1.779914
Train Epoch: 2 [1920/2540 (75%)]	Loss: 1.698332
Train Epoch: 3 [0/2540 (0%)]	Loss: 1.695987
Train Epoch: 3 [640/2540 (25%)]	Loss: 1.612298
Train Epoch: 3 [1280/2540 (50%)]	Loss: 1.546044
Train Epoch: 3 [1920/2540 (75%)]	Loss: 1.477604
Train Epoch: 4 [0/2540 (0%)]	Loss: 1.284204
Train Epoch: 4 [640/2540 (25%)]	Loss: 1.334915
Train Epoch: 4 [1280/2540 (50%)]	Loss: 1.261232
Train Epoch: 4 [1920/2540 (75%)]	Loss: 1.060399
Train Epoch: 5 [0/2540 (0%)]	Loss: 1.493942
Train Epoch: 5 [640/2540 (25%)]	Loss: 1.352840
Train Epoch: 5 [1280/2540 (50%)]	Loss: 1.221062
Train Epoch: 5 [1920/2540 (75%)]	Loss: 1.009544
Train Epoch: 6 [0/2540 (0%)]	Loss: 0.

c:\Users\micha\anaconda3\Lib\site-packages\torch\nn\_reduction.py:42: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))



Test set: Avg. loss: 1.6214, Accuracy: 4965/10000 (50%)

Round 2/8
Training client 1
Train Epoch: 1 [0/2540 (0%)]	Loss: 0.941165
Train Epoch: 1 [640/2540 (25%)]	Loss: 0.907588
Train Epoch: 1 [1280/2540 (50%)]	Loss: 0.841938
Train Epoch: 1 [1920/2540 (75%)]	Loss: 0.663696
Train Epoch: 2 [0/2540 (0%)]	Loss: 0.669343
Train Epoch: 2 [640/2540 (25%)]	Loss: 0.831106
Train Epoch: 2 [1280/2540 (50%)]	Loss: 0.725941
Train Epoch: 2 [1920/2540 (75%)]	Loss: 0.746885
Train Epoch: 3 [0/2540 (0%)]	Loss: 0.549645
Train Epoch: 3 [640/2540 (25%)]	Loss: 0.473259
Train Epoch: 3 [1280/2540 (50%)]	Loss: 0.709710
Train Epoch: 3 [1920/2540 (75%)]	Loss: 0.701819
Train Epoch: 4 [0/2540 (0%)]	Loss: 0.518392
Train Epoch: 4 [640/2540 (25%)]	Loss: 0.445481
Train Epoch: 4 [1280/2540 (50%)]	Loss: 0.636845
Train Epoch: 4 [1920/2540 (75%)]	Loss: 0.651908
Train Epoch: 5 [0/2540 (0%)]	Loss: 0.452915
Train Epoch: 5 [640/2540 (25%)]	Loss: 0.570168
Train Epoch: 5 [1280/2540 (50%)]	Loss: 0.702523
Train Epoch: 5 [1920/2540 (

c:\Users\micha\anaconda3\Lib\site-packages\torch\nn\_reduction.py:42: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))



Test set: Avg. loss: 1.0889, Accuracy: 6496/10000 (65%)

Round 3/8
Training client 1
Train Epoch: 1 [0/2540 (0%)]	Loss: 0.589503
Train Epoch: 1 [640/2540 (25%)]	Loss: 0.404721
Train Epoch: 1 [1280/2540 (50%)]	Loss: 0.292139
Train Epoch: 1 [1920/2540 (75%)]	Loss: 0.429883
Train Epoch: 2 [0/2540 (0%)]	Loss: 0.411186
Train Epoch: 2 [640/2540 (25%)]	Loss: 0.391014
Train Epoch: 2 [1280/2540 (50%)]	Loss: 0.577380
Train Epoch: 2 [1920/2540 (75%)]	Loss: 0.539064
Train Epoch: 3 [0/2540 (0%)]	Loss: 0.348930
Train Epoch: 3 [640/2540 (25%)]	Loss: 0.480886
Train Epoch: 3 [1280/2540 (50%)]	Loss: 0.294926
Train Epoch: 3 [1920/2540 (75%)]	Loss: 0.386219
Train Epoch: 4 [0/2540 (0%)]	Loss: 0.299804
Train Epoch: 4 [640/2540 (25%)]	Loss: 0.463784
Train Epoch: 4 [1280/2540 (50%)]	Loss: 0.392582
Train Epoch: 4 [1920/2540 (75%)]	Loss: 0.490047
Train Epoch: 5 [0/2540 (0%)]	Loss: 0.360377
Train Epoch: 5 [640/2540 (25%)]	Loss: 0.491496
Train Epoch: 5 [1280/2540 (50%)]	Loss: 0.271054
Train Epoch: 5 [1920/2540 (

...


Test set: Avg. loss: 0.6194, Accuracy: 8571/10000 (86%)

Round 7/8
Training client 1
Train Epoch: 1 [0/2540 (0%)]	Loss: 0.041976
Train Epoch: 1 [640/2540 (25%)]	Loss: 0.024464
Train Epoch: 1 [1280/2540 (50%)]	Loss: 0.049928
Train Epoch: 1 [1920/2540 (75%)]	Loss: 0.019520
Train Epoch: 2 [0/2540 (0%)]	Loss: 0.008859
Train Epoch: 2 [640/2540 (25%)]	Loss: 0.036862
Train Epoch: 2 [1280/2540 (50%)]	Loss: 0.025700
Train Epoch: 2 [1920/2540 (75%)]	Loss: 0.007943
Train Epoch: 3 [0/2540 (0%)]	Loss: 0.004485
Train Epoch: 3 [640/2540 (25%)]	Loss: 0.007187
Train Epoch: 3 [1280/2540 (50%)]	Loss: 0.001637
Train Epoch: 3 [1920/2540 (75%)]	Loss: 0.011153
Train Epoch: 4 [0/2540 (0%)]	Loss: 0.008938
Train Epoch: 4 [640/2540 (25%)]	Loss: 0.003473
Train Epoch: 4 [1280/2540 (50%)]	Loss: 0.005548
Train Epoch: 4 [1920/2540 (75%)]	Loss: 0.004663
Train Epoch: 5 [0/2540 (0%)]	Loss: 0.002505
Train Epoch: 5 [640/2540 (25%)]	Loss: 0.006086
Train Epoch: 5 [1280/2540 (50%)]	Loss: 0.007658
Train Epoch: 5 [1920/2540 (

c:\Users\micha\anaconda3\Lib\site-packages\torch\nn\_reduction.py:42: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))



Test set: Avg. loss: 0.6180, Accuracy: 8579/10000 (86%)

Round 8/8
Training client 1
Train Epoch: 1 [0/2540 (0%)]	Loss: 0.022200
Train Epoch: 1 [640/2540 (25%)]	Loss: 0.016352
Train Epoch: 1 [1280/2540 (50%)]	Loss: 0.006296
Train Epoch: 1 [1920/2540 (75%)]	Loss: 0.021288
Train Epoch: 2 [0/2540 (0%)]	Loss: 0.008086
Train Epoch: 2 [640/2540 (25%)]	Loss: 0.012714
Train Epoch: 2 [1280/2540 (50%)]	Loss: 0.019763
Train Epoch: 2 [1920/2540 (75%)]	Loss: 0.005094
Train Epoch: 3 [0/2540 (0%)]	Loss: 0.006262
Train Epoch: 3 [640/2540 (25%)]	Loss: 0.006634
Train Epoch: 3 [1280/2540 (50%)]	Loss: 0.004914
Train Epoch: 3 [1920/2540 (75%)]	Loss: 0.006391
Train Epoch: 4 [0/2540 (0%)]	Loss: 0.003777
Train Epoch: 4 [640/2540 (25%)]	Loss: 0.004588
Train Epoch: 4 [1280/2540 (50%)]	Loss: 0.008024
Train Epoch: 4 [1920/2540 (75%)]	Loss: 0.005524
Train Epoch: 5 [0/2540 (0%)]	Loss: 0.003442
Train Epoch: 5 [640/2540 (25%)]	Loss: 0.003101
Train Epoch: 5 [1280/2540 (50%)]	Loss: 0.005807
Train Epoch: 5 [1920/2540 (

c:\Users\micha\anaconda3\Lib\site-packages\torch\nn\_reduction.py:42: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))



Test set: Avg. loss: 0.6206, Accuracy: 8582/10000 (86%)



In [10]:
print("Final Results (Non-Clustered):", results)
print("Final Results (Clustered):", clusteredResults)

Final Results (Non-Clustered): {'classic': {'NoCluster': {'losses': [0.6709944795131684], 'accuracy': [79.7], 'precision': [0.8043892536564592], 'recall': [0.797], 'f1': [0.7968143720115093], 'trainingTime': [141.49312472343445]}}, 'pca': {}, 'autoencoder': {}}
Final Results (Clustered): {'classic': {2: {'losses': [0.7907732093334198, 0.8398547622203827, 0.8573668549537659, 0.8783597696304322, 0.8969815037727356, 0.9100769341468811, 0.9346470438957214, 0.9650899912834168], 'accuracy': [77.25, 76.39, 76.45, 76.53, 76.55, 76.59, 76.52, 76.4], 'precision': [0.7969475022750417, 0.7938828290001663, 0.7929634077899974, 0.7936628035598224, 0.7938666819596314, 0.792592641917141, 0.7925675153749545, 0.7928764484878046], 'recall': [0.7725000000000001, 0.7639, 0.7645, 0.7653000000000001, 0.7655000000000001, 0.7659, 0.7652, 0.764], 'f1': [0.7705422584191478, 0.7615035212519925, 0.7622018219756702, 0.7630920986450184, 0.763394291256817, 0.7638294095461351, 0.76313265164566, 0.7617446365747026], 'tr

# PCA

In [11]:
trainingset_pca = train_loader_pca.dataset
trial_model_pca_strong = MultilayerPerceptron()
global_model_pca_strong = MultilayerPerceptron()

In [12]:
partitioned_data_pca = partition.balanced_dirichlet_partition(trainingset_pca, partitions_number=num_clients, alpha=alpha)

pca_client_loaders = []
local_models_pca_strong = [copy.deepcopy(global_model_pca_strong) for _ in range(num_clients)]

for client_idx, client_indices in partitioned_data_pca.items():
    client_data = [trainingset_pca[i][0] for i in client_indices]  
    client_labels = [trainingset_pca[i][1] for i in client_indices]  
    
    client_data = torch.stack(client_data, dim=0)
    client_data = client_data.view(client_data.size(0), -1)  
    
    pca = PCADigitReducer(100)
    client_data_reduced = pca.fit_transform(client_data.numpy())  
    
    client_data_reconstructed_np = pca.inverse_transform(client_data_reduced) 
    client_data_reconstructed = torch.tensor(client_data_reconstructed_np, dtype=torch.float32)
    
    client_data_reconstructed = client_data_reconstructed.view(-1, 1, 28, 28)
    client_data_reconstructed = (client_data_reconstructed - 0.2860) / 0.3204  
    
    client_dataset_pca = CustomTensorDataset(client_data_reconstructed, torch.tensor(client_labels))
    pca_client_loaders.append(DataLoader(client_dataset_pca, batch_size=batch_size_train, shuffle=True))


rounds_pca = 8
for round_idx in range(rounds_pca):
    print(f"Round {round_idx + 1}/{rounds_pca}")
    t1=time.time()

    local_weights_pca = []
    for client_idx, client_model in enumerate(local_models_pca_strong):
        print(f"Training client {client_idx + 1}")
        
        optimizer = optim.SGD(client_model.parameters(), lr=learning_rate,
                      momentum=momentum)

        train_losses = []
        train_counter = []


        for epoch in range(1, n_epochs + 1):  
            train_fashion(epoch, client_model, pca_client_loaders[client_idx], optimizer, log_interval, train_losses, train_counter)
        
        client_weights = [param.data.numpy() for param in client_model.parameters()]
        local_weights_pca.append(client_weights)
        

    global_weights_pca = federated_averaging(local_weights_pca)

    distribute_global_model(global_weights_pca,local_models_pca_strong,single=False)

    distribute_global_model(global_weights_pca,global_model_pca_strong,single=True)
    test_losses = []
    test_fashion(global_model_pca_strong,test_loader_pca,test_losses)
    t2= time.time()

    test_accuracies_pca = []
    correct = 0
    all_preds = []
    all_targets = []
    with torch.no_grad():
        for data, target in test_loader_pca:
            data = data.view(data.shape[0], -1)
            output = global_model_pca_strong(data)
            pred = output.data.max(1, keepdim=True)[1]
            all_preds.extend(pred.cpu().numpy().flatten())
            all_targets.extend(target.cpu().numpy().flatten())
            correct += pred.eq(target.data.view_as(pred)).sum().item()
    
    accuracy = 100. * correct / len(test_loader_pca.dataset)
    test_accuracies_pca.append(accuracy)
    precision = precision_score(all_targets, all_preds, average='macro')
    recall = recall_score(all_targets, all_preds, average='macro')
    f1 = f1_score(all_targets, all_preds, average='macro')
    # Save results for non-clustered classic
    results["pca"]["NoCluster"] = {"losses": [], "accuracy": [], "precision": [], "recall": [], "f1": [], "trainingTime": []}

    results["pca"]["NoCluster"]["losses"].extend(test_losses)
    results["pca"]["NoCluster"]["accuracy"].extend(test_accuracies_pca)
    results["pca"]["NoCluster"]["precision"].append(precision)
    results["pca"]["NoCluster"]["recall"].append(recall)
    results["pca"]["NoCluster"]["f1"].append(f1)
    results["pca"]["NoCluster"]["trainingTime"].append(t2-t1)

    ######################
for num_cluster in num_clusters:
    import cluster2

    targets = trainingset.targets
    num_classes = len(set(targets)) 
    clients = [cluster2.FederatedClient(cid, indices, targets, num_classes) for cid, indices in partitioned_data_pca.items()]
    client_distributions = [client.compute_label_distribution() for client in clients]
    server = cluster2.FederatedClusterServer(num_cluster)
    aggregated_data = server.aggregate_client_data(client_distributions)
    clustered_data = server.perform_greedy_clustering(aggregated_data, partitioned_data_pca)
    
    partitioned_data_pca_clustered = clustered_data

    pca_client_loaders_clustered = []

    # Apply PCA after clustering
    for client_idx, client_indices in partitioned_data_pca_clustered.items():
        client_data = [trainingset_pca[i][0] for i in client_indices]  
        client_labels = [trainingset_pca[i][1] for i in client_indices]  

        client_data = torch.stack(client_data, dim=0)
        client_data = client_data.view(client_data.size(0), -1)  
        
        pca = PCADigitReducer(100)
        client_data_reduced = pca.fit_transform(client_data.numpy())  

        client_data_reconstructed_np = pca.inverse_transform(client_data_reduced)  
        client_data_reconstructed = torch.tensor(client_data_reconstructed_np, dtype=torch.float32)
        
        client_data_reconstructed = client_data_reconstructed.view(-1, 1, 28, 28)
        client_data_reconstructed = (client_data_reconstructed - 0.2860) / 0.3204  

        client_dataset_pca_clustered = CustomTensorDataset(client_data_reconstructed, torch.tensor(client_labels))
        pca_client_loaders_clustered.append(DataLoader(client_dataset_pca_clustered, batch_size=batch_size_train, shuffle=True))


    for round_idx in range(rounds_classic):
        print(f"Round {round_idx + 1}/{rounds_classic}")
        t1=time.time()

        local_weights_pca = []
        for client_idx, client_model in enumerate(local_models_pca_strong[0:num_cluster]):
            print(f"Training client {client_idx + 1}")
            
            optimizer = optim.SGD(client_model.parameters(), lr=learning_rate,
                          momentum=momentum)
    
            train_losses = []
            train_counter = []
    
    
            for epoch in range(1, n_epochs + 1):  
                train_fashion(epoch, client_model, pca_client_loaders[client_idx], optimizer, log_interval, train_losses, train_counter)
            
            client_weights = [param.data.numpy() for param in client_model.parameters()]
            local_weights_pca.append(client_weights)
            
    
        global_weights_pca = federated_averaging(local_weights_pca)
    
        distribute_global_model(global_weights_pca,local_models_pca_strong,single=False)
    
        distribute_global_model(global_weights_pca,global_model_pca_strong,single=True)
        test_losses = []
        test_fashion(global_model_pca_strong,test_loader_pca,test_losses)
        t2= time.time()
    
        test_accuracies_pca = []
        correct = 0
        all_preds = []
        all_targets = []
        with torch.no_grad():
            for data, target in test_loader_pca:
                data = data.view(data.shape[0], -1)
                output = global_model_pca_strong(data)
                pred = output.data.max(1, keepdim=True)[1]
                all_preds.extend(pred.cpu().numpy().flatten())
                all_targets.extend(target.cpu().numpy().flatten())
                correct += pred.eq(target.data.view_as(pred)).sum().item()
        
        accuracy = 100. * correct / len(test_loader_pca.dataset)
        test_accuracies_pca.append(accuracy)
        precision = precision_score(all_targets, all_preds, average='macro')
        recall = recall_score(all_targets, all_preds, average='macro')
        f1 = f1_score(all_targets, all_preds, average='macro')

        # Save results for clustered classic
        if num_cluster not in clusteredResults["pca"]:
            clusteredResults["pca"][num_cluster] = {"losses": [], "accuracy": [], "precision": [], "recall": [], "f1": [], "trainingTime": []}

        clusteredResults["pca"][num_cluster]["losses"].extend(test_losses)
        clusteredResults["pca"][num_cluster]["accuracy"].extend(test_accuracies_pca)
        clusteredResults["pca"][num_cluster]["precision"].append(precision)
        clusteredResults["pca"][num_cluster]["recall"].append(recall)
        clusteredResults["pca"][num_cluster]["f1"].append(f1)
        clusteredResults["pca"][num_cluster]["trainingTime"].append(t2-t1)

Round 1/8
Training client 1
Train Epoch: 1 [0/2540 (0%)]	Loss: 2.297100
Train Epoch: 1 [640/2540 (25%)]	Loss: 2.131598
Train Epoch: 1 [1280/2540 (50%)]	Loss: 1.719335
Train Epoch: 1 [1920/2540 (75%)]	Loss: 1.370041
Train Epoch: 2 [0/2540 (0%)]	Loss: 1.220191
Train Epoch: 2 [640/2540 (25%)]	Loss: 1.080892
Train Epoch: 2 [1280/2540 (50%)]	Loss: 1.079648
Train Epoch: 2 [1920/2540 (75%)]	Loss: 0.903145
Train Epoch: 3 [0/2540 (0%)]	Loss: 1.094543
Train Epoch: 3 [640/2540 (25%)]	Loss: 0.731342
Train Epoch: 3 [1280/2540 (50%)]	Loss: 0.904400
Train Epoch: 3 [1920/2540 (75%)]	Loss: 0.856473
Train Epoch: 4 [0/2540 (0%)]	Loss: 0.706082
Train Epoch: 4 [640/2540 (25%)]	Loss: 0.888530
Train Epoch: 4 [1280/2540 (50%)]	Loss: 0.613692
Train Epoch: 4 [1920/2540 (75%)]	Loss: 0.920461
Train Epoch: 5 [0/2540 (0%)]	Loss: 0.531506
Train Epoch: 5 [640/2540 (25%)]	Loss: 0.670591
Train Epoch: 5 [1280/2540 (50%)]	Loss: 0.964802
Train Epoch: 5 [1920/2540 (75%)]	Loss: 0.769213
Train Epoch: 6 [0/2540 (0%)]	Loss: 0.

c:\Users\micha\anaconda3\Lib\site-packages\torch\nn\_reduction.py:42: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))



Test set: Avg. loss: 1.8830, Accuracy: 5396/10000 (54%)

Round 2/8
Training client 1
Train Epoch: 1 [0/2540 (0%)]	Loss: 0.516746
Train Epoch: 1 [640/2540 (25%)]	Loss: 0.453229
Train Epoch: 1 [1280/2540 (50%)]	Loss: 0.393646
Train Epoch: 1 [1920/2540 (75%)]	Loss: 0.605302
Train Epoch: 2 [0/2540 (0%)]	Loss: 0.460968
Train Epoch: 2 [640/2540 (25%)]	Loss: 0.386397
Train Epoch: 2 [1280/2540 (50%)]	Loss: 0.569124
Train Epoch: 2 [1920/2540 (75%)]	Loss: 0.219495
Train Epoch: 3 [0/2540 (0%)]	Loss: 0.227232
Train Epoch: 3 [640/2540 (25%)]	Loss: 0.267425
Train Epoch: 3 [1280/2540 (50%)]	Loss: 0.342869
Train Epoch: 3 [1920/2540 (75%)]	Loss: 0.354231
Train Epoch: 4 [0/2540 (0%)]	Loss: 0.361439
Train Epoch: 4 [640/2540 (25%)]	Loss: 0.381900
Train Epoch: 4 [1280/2540 (50%)]	Loss: 0.357825
Train Epoch: 4 [1920/2540 (75%)]	Loss: 0.282469
Train Epoch: 5 [0/2540 (0%)]	Loss: 0.310468
Train Epoch: 5 [640/2540 (25%)]	Loss: 0.148882
Train Epoch: 5 [1280/2540 (50%)]	Loss: 0.174529
Train Epoch: 5 [1920/2540 (

c:\Users\micha\anaconda3\Lib\site-packages\torch\nn\_reduction.py:42: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))



Test set: Avg. loss: 1.5260, Accuracy: 6796/10000 (68%)

Round 3/8
Training client 1
Train Epoch: 1 [0/2540 (0%)]	Loss: 0.282442
Train Epoch: 1 [640/2540 (25%)]	Loss: 0.201081
Train Epoch: 1 [1280/2540 (50%)]	Loss: 0.307056
Train Epoch: 1 [1920/2540 (75%)]	Loss: 0.133883
Train Epoch: 2 [0/2540 (0%)]	Loss: 0.302738
Train Epoch: 2 [640/2540 (25%)]	Loss: 0.201179
Train Epoch: 2 [1280/2540 (50%)]	Loss: 0.248618
Train Epoch: 2 [1920/2540 (75%)]	Loss: 0.266388
Train Epoch: 3 [0/2540 (0%)]	Loss: 0.235121
Train Epoch: 3 [640/2540 (25%)]	Loss: 0.307152
Train Epoch: 3 [1280/2540 (50%)]	Loss: 0.114558
Train Epoch: 3 [1920/2540 (75%)]	Loss: 0.220739
Train Epoch: 4 [0/2540 (0%)]	Loss: 0.129508
Train Epoch: 4 [640/2540 (25%)]	Loss: 0.154045
Train Epoch: 4 [1280/2540 (50%)]	Loss: 0.138810
Train Epoch: 4 [1920/2540 (75%)]	Loss: 0.296597
Train Epoch: 5 [0/2540 (0%)]	Loss: 0.098418
Train Epoch: 5 [640/2540 (25%)]	Loss: 0.143851
Train Epoch: 5 [1280/2540 (50%)]	Loss: 0.155233
Train Epoch: 5 [1920/2540 (

...


Test set: Avg. loss: 0.7569, Accuracy: 7766/10000 (78%)

Round 7/8
Training client 1
Train Epoch: 1 [0/2540 (0%)]	Loss: 0.026095
Train Epoch: 1 [640/2540 (25%)]	Loss: 0.004588
Train Epoch: 1 [1280/2540 (50%)]	Loss: 0.001001
Train Epoch: 1 [1920/2540 (75%)]	Loss: 0.016388
Train Epoch: 2 [0/2540 (0%)]	Loss: 0.006151
Train Epoch: 2 [640/2540 (25%)]	Loss: 0.003167
Train Epoch: 2 [1280/2540 (50%)]	Loss: 0.006361
Train Epoch: 2 [1920/2540 (75%)]	Loss: 0.009509
Train Epoch: 3 [0/2540 (0%)]	Loss: 0.002907
Train Epoch: 3 [640/2540 (25%)]	Loss: 0.003239
Train Epoch: 3 [1280/2540 (50%)]	Loss: 0.005732
Train Epoch: 3 [1920/2540 (75%)]	Loss: 0.001597
Train Epoch: 4 [0/2540 (0%)]	Loss: 0.002499
Train Epoch: 4 [640/2540 (25%)]	Loss: 0.002092
Train Epoch: 4 [1280/2540 (50%)]	Loss: 0.002643
Train Epoch: 4 [1920/2540 (75%)]	Loss: 0.002442
Train Epoch: 5 [0/2540 (0%)]	Loss: 0.001005
Train Epoch: 5 [640/2540 (25%)]	Loss: 0.002181
Train Epoch: 5 [1280/2540 (50%)]	Loss: 0.002262
Train Epoch: 5 [1920/2540 (

c:\Users\micha\anaconda3\Lib\site-packages\torch\nn\_reduction.py:42: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))



Test set: Avg. loss: 0.7588, Accuracy: 7754/10000 (78%)

Round 8/8
Training client 1
Train Epoch: 1 [0/2540 (0%)]	Loss: 0.009654
Train Epoch: 1 [640/2540 (25%)]	Loss: 0.026662
Train Epoch: 1 [1280/2540 (50%)]	Loss: 0.016929
Train Epoch: 1 [1920/2540 (75%)]	Loss: 0.008506
Train Epoch: 2 [0/2540 (0%)]	Loss: 0.041763
Train Epoch: 2 [640/2540 (25%)]	Loss: 0.022572
Train Epoch: 2 [1280/2540 (50%)]	Loss: 0.010244
Train Epoch: 2 [1920/2540 (75%)]	Loss: 0.015744
Train Epoch: 3 [0/2540 (0%)]	Loss: 0.001010
Train Epoch: 3 [640/2540 (25%)]	Loss: 0.003163
Train Epoch: 3 [1280/2540 (50%)]	Loss: 0.001755
Train Epoch: 3 [1920/2540 (75%)]	Loss: 0.001776
Train Epoch: 4 [0/2540 (0%)]	Loss: 0.001069
Train Epoch: 4 [640/2540 (25%)]	Loss: 0.000943
Train Epoch: 4 [1280/2540 (50%)]	Loss: 0.002065
Train Epoch: 4 [1920/2540 (75%)]	Loss: 0.001813
Train Epoch: 5 [0/2540 (0%)]	Loss: 0.001013
Train Epoch: 5 [640/2540 (25%)]	Loss: 0.001687
Train Epoch: 5 [1280/2540 (50%)]	Loss: 0.000727
Train Epoch: 5 [1920/2540 (

c:\Users\micha\anaconda3\Lib\site-packages\torch\nn\_reduction.py:42: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))



Test set: Avg. loss: 0.7595, Accuracy: 7754/10000 (78%)



In [13]:
print("Final Results (Non-Clustered):", results)
print("Final Results (Clustered):", clusteredResults)

Final Results (Non-Clustered): {'classic': {'NoCluster': {'losses': [0.6709944795131684], 'accuracy': [79.7], 'precision': [0.8043892536564592], 'recall': [0.797], 'f1': [0.7968143720115093], 'trainingTime': [141.49312472343445]}}, 'pca': {'NoCluster': {'losses': [1.0360757004737855], 'accuracy': [75.4], 'precision': [0.7910034458189418], 'recall': [0.754], 'f1': [0.7546677147573707], 'trainingTime': [24.850576400756836]}}, 'autoencoder': {}}
Final Results (Clustered): {'classic': {2: {'losses': [0.7907732093334198, 0.8398547622203827, 0.8573668549537659, 0.8783597696304322, 0.8969815037727356, 0.9100769341468811, 0.9346470438957214, 0.9650899912834168], 'accuracy': [77.25, 76.39, 76.45, 76.53, 76.55, 76.59, 76.52, 76.4], 'precision': [0.7969475022750417, 0.7938828290001663, 0.7929634077899974, 0.7936628035598224, 0.7938666819596314, 0.792592641917141, 0.7925675153749545, 0.7928764484878046], 'recall': [0.7725000000000001, 0.7639, 0.7645, 0.7653000000000001, 0.7655000000000001, 0.7659,

# Autoencoder

In [12]:
# Autoencoder
trainingset_auto = train_loader_pca.dataset
trial_model_auto_strong = MultilayerPerceptron()
global_model_auto_strong = MultilayerPerceptron()
autoencoder.eval()

Autoencoder2(
  (encoder): Sequential(
    (0): Conv2d(1, 32, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (1): ReLU()
    (2): Conv2d(32, 32, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (3): ReLU()
    (4): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
    (5): BatchNorm2d(32, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (6): Conv2d(32, 32, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (7): ReLU()
    (8): Conv2d(32, 32, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (9): ReLU()
    (10): Conv2d(32, 2, kernel_size=(2, 2), stride=(1, 1), padding=(1, 1))
    (11): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
    (12): BatchNorm2d(2, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (13): Flatten(start_dim=1, end_dim=-1)
    (14): Linear(in_features=98, out_features=100, bias=True)
    (15): ReLU()
  )
  (decoder): Sequential(
    (0): Linear(in_featur

In [13]:

partitioned_data_auto = partition.balanced_dirichlet_partition(trainingset_auto, partitions_number=num_clients, alpha=alpha)
auto_client_loaders = [
    DataLoader(Subset(trainingset_auto, indices), batch_size=batch_size_train, shuffle=True)
    for indices in partitioned_data_auto.values()
]

auto_client_loader_reduced = []
for i,client in enumerate(auto_client_loaders):
    
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    latent_features, labels = reduce_dimensions2(auto_client_loaders[i], autoencoder.encoder, device)
    latent_features = latent_features.detach()

    reconstructed_images = autoencoder.decoder(latent_features.to(device))  
    reconstructed_images = reconstructed_images.view(-1, 1, 28, 28)  # Reshape to [batch_size, channels, height, width]

    reconstructed_dataset = CustomTensorDataset(reconstructed_images.cpu(), labels)  
    reduced_train_loader_auto = DataLoader(reconstructed_dataset, batch_size=batch_size_train, shuffle=True)
    auto_client_loader_reduced.append(reduced_train_loader_auto)


local_model_autoencoder_strong = [copy.deepcopy(global_model_auto_strong) for _ in range(num_clients)]

rounds_auto = 8
for round_idx in range(rounds_auto):
    print(f"Round {round_idx + 1}/{rounds_auto}")
    t1=time.time()
    
    local_weights_auto = []
    for client_idx, client_model in enumerate(local_model_autoencoder_strong):
        print(f"Training client {client_idx + 1}")
        
        optimizer = optim.SGD(client_model.parameters(), lr=learning_rate, momentum=momentum)
        
        train_losses = []
        train_counter = []
    
        for epoch in range(1, n_epochs + 1):  
            train_fashion(epoch, client_model, auto_client_loader_reduced[client_idx], optimizer, log_interval, train_losses, train_counter)
        
        client_weights = [param.data.numpy() for param in client_model.parameters()]
        local_weights_auto.append(client_weights)
    
    global_weights_auto = federated_averaging(local_weights_auto)
    
    distribute_global_model(global_weights_auto, local_model_autoencoder_strong, single=False)
    distribute_global_model(global_weights_auto, global_model_auto_strong, single=True)
    
    test_losses = []
    test_fashion(global_model_auto_strong, test_loader_auto, test_losses)
    t2= time.time()
    
    test_accuracies_auto = []
    all_preds = []
    all_targets = []
    with torch.no_grad():
        for data, target in test_loader_auto:
            data = data.view(data.shape[0], -1)
            output = global_model_auto_strong(data)
            pred = output.data.max(1, keepdim=True)[1]  # Get the predicted class
            
            all_preds.extend(pred.cpu().numpy().flatten())  # Store predictions
            all_targets.extend(target.cpu().numpy().flatten())  # Store true labels

    # Compute accuracy
    correct = sum(p == t for p, t in zip(all_preds, all_targets))
    accuracy = 100. * correct / len(all_targets)
    test_accuracies_auto.append(accuracy)
    precision = precision_score(all_targets, all_preds, average='macro')  # or 'weighted' for imbalance
    recall = recall_score(all_targets, all_preds, average='macro')
    f1 = f1_score(all_targets, all_preds, average='macro')
    
    # Save results for non-clustered classic
    results["autoencoder"]["NoCluster"] = {"losses": [], "accuracy": [], "precision": [], "recall": [], "f1": [], "trainingTime": []}
    
    results["autoencoder"]["NoCluster"]["losses"].extend(test_losses)
    results["autoencoder"]["NoCluster"]["accuracy"].extend(test_accuracies_auto)
    results["autoencoder"]["NoCluster"]["precision"].append(precision)
    results["autoencoder"]["NoCluster"]["recall"].append(recall)
    results["autoencoder"]["NoCluster"]["f1"].append(f1)
    results["autoencoder"]["NoCluster"]["trainingTime"].append(t2-t1)

    ######################
    # Clustering process
for num_cluster in num_clusters:
    import cluster2

    targets = trainingset.targets
    num_classes = len(set(targets)) 
    clients = [cluster2.FederatedClient(cid, indices, targets, num_classes) for cid, indices in partitioned_data_auto.items()]
    client_distributions = [client.compute_label_distribution() for client in clients]
    server = cluster2.FederatedClusterServer(num_cluster)
    aggregated_data = server.aggregate_client_data(client_distributions)
    clustered_data = server.perform_greedy_clustering(aggregated_data, partitioned_data_auto)
    
    partitioned_data_auto_clustered = clustered_data
    
    auto_client_loaders_clustered = [
        DataLoader(Subset(trainingset_auto, indices), batch_size=batch_size_train, shuffle=True)
        for indices in partitioned_data_auto_clustered.values()
    ]

    auto_client_loader_reduced = []

    for i,client in enumerate(auto_client_loaders_clustered):
        
        device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
        latent_features, labels = reduce_dimensions2(auto_client_loaders_clustered[i], autoencoder.encoder, device)
        latent_features = latent_features.detach()

        reconstructed_images = autoencoder.decoder(latent_features.to(device))  
        reconstructed_images = reconstructed_images.view(-1, 1, 28, 28)  # Reshape to [batch_size, channels, height, width]

        reconstructed_dataset = CustomTensorDataset(reconstructed_images.cpu(), labels)  
        reduced_train_loader_auto = DataLoader(reconstructed_dataset, batch_size=batch_size_train, shuffle=True)
        auto_client_loader_reduced.append(reduced_train_loader_auto)


    
    for round_idx in range(rounds_auto):
        print(f"Round {round_idx + 1}/{rounds_auto}")
        t1=time.time()
        
        local_weights_auto = []
        for client_idx, client_model in enumerate(local_model_autoencoder_strong[0:num_cluster]):
            print(f"Training client {client_idx + 1}")
            
            optimizer = optim.SGD(client_model.parameters(), lr=learning_rate, momentum=momentum)
            
            train_losses = []
            train_counter = []
        
            for epoch in range(1, n_epochs + 1):  
                train_fashion(epoch, client_model, auto_client_loader_reduced[client_idx], optimizer, log_interval, train_losses, train_counter)
            
            client_weights = [param.data.numpy() for param in client_model.parameters()]
            local_weights_auto.append(client_weights)
        
        global_weights_auto = federated_averaging(local_weights_auto)
        
        distribute_global_model(global_weights_auto, local_model_autoencoder_strong, single=False)
        distribute_global_model(global_weights_auto, global_model_auto_strong, single=True)
        
        test_losses = []
        test_fashion(global_model_auto_strong, test_loader_auto, test_losses)
        t2= time.time()
        
        test_accuracies_auto = []
        all_preds = []
        all_targets = []
        with torch.no_grad():
            for data, target in test_loader_auto:
                data = data.view(data.shape[0], -1)
                output = global_model_auto_strong(data)
                pred = output.data.max(1, keepdim=True)[1]
                all_preds.extend(pred.cpu().numpy().flatten())
                all_targets.extend(target.cpu().numpy().flatten())
        
        correct = sum(p == t for p, t in zip(all_preds, all_targets))
        accuracy = 100. * correct / len(all_targets)
        test_accuracies_auto.append(accuracy)
        precision = precision_score(all_targets, all_preds, average='macro')
        recall = recall_score(all_targets, all_preds, average='macro')
        f1 = f1_score(all_targets, all_preds, average='macro')
        
        # Save results for clustered classic
        if num_cluster not in clusteredResults["autoencoder"]:
            clusteredResults["autoencoder"][num_cluster] = {"losses": [], "accuracy": [], "precision": [], "recall": [], "f1": [], "trainingTime": []}

        clusteredResults["autoencoder"][num_cluster]["losses"].extend(test_losses)
        clusteredResults["autoencoder"][num_cluster]["accuracy"].extend(test_accuracies_auto)
        clusteredResults["autoencoder"][num_cluster]["precision"].append(precision)
        clusteredResults["autoencoder"][num_cluster]["recall"].append(recall)
        clusteredResults["autoencoder"][num_cluster]["f1"].append(f1)
        clusteredResults["autoencoder"][num_cluster]["trainingTime"].append(t2-t1)

Round 1/8
Training client 1
Train Epoch: 1 [0/2540 (0%)]	Loss: 2.296154
Train Epoch: 1 [640/2540 (25%)]	Loss: 2.261732
Train Epoch: 1 [1280/2540 (50%)]	Loss: 2.217870
Train Epoch: 1 [1920/2540 (75%)]	Loss: 2.140033
Train Epoch: 2 [0/2540 (0%)]	Loss: 2.116955
Train Epoch: 2 [640/2540 (25%)]	Loss: 1.983274
Train Epoch: 2 [1280/2540 (50%)]	Loss: 1.942771
Train Epoch: 2 [1920/2540 (75%)]	Loss: 1.928612
Train Epoch: 3 [0/2540 (0%)]	Loss: 1.697686
Train Epoch: 3 [640/2540 (25%)]	Loss: 1.604860
Train Epoch: 3 [1280/2540 (50%)]	Loss: 1.540252
Train Epoch: 3 [1920/2540 (75%)]	Loss: 1.288633
Train Epoch: 4 [0/2540 (0%)]	Loss: 1.540906
Train Epoch: 4 [640/2540 (25%)]	Loss: 1.286929
Train Epoch: 4 [1280/2540 (50%)]	Loss: 1.422774
Train Epoch: 4 [1920/2540 (75%)]	Loss: 1.293766
Train Epoch: 5 [0/2540 (0%)]	Loss: 1.284686
Train Epoch: 5 [640/2540 (25%)]	Loss: 1.283415
Train Epoch: 5 [1280/2540 (50%)]	Loss: 1.290174
Train Epoch: 5 [1920/2540 (75%)]	Loss: 1.498750
Train Epoch: 6 [0/2540 (0%)]	Loss: 1.

c:\Users\micha\anaconda3\Lib\site-packages\torch\nn\_reduction.py:42: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))



Test set: Avg. loss: 1.6252, Accuracy: 4699/10000 (47%)

Round 2/8
Training client 1
Train Epoch: 1 [0/2540 (0%)]	Loss: 1.037919
Train Epoch: 1 [640/2540 (25%)]	Loss: 0.778004
Train Epoch: 1 [1280/2540 (50%)]	Loss: 0.667605
Train Epoch: 1 [1920/2540 (75%)]	Loss: 0.654483
Train Epoch: 2 [0/2540 (0%)]	Loss: 0.942384
Train Epoch: 2 [640/2540 (25%)]	Loss: 0.718769
Train Epoch: 2 [1280/2540 (50%)]	Loss: 0.574889
Train Epoch: 2 [1920/2540 (75%)]	Loss: 0.821141
Train Epoch: 3 [0/2540 (0%)]	Loss: 0.612634
Train Epoch: 3 [640/2540 (25%)]	Loss: 0.575761
Train Epoch: 3 [1280/2540 (50%)]	Loss: 0.602628
Train Epoch: 3 [1920/2540 (75%)]	Loss: 0.576558
Train Epoch: 4 [0/2540 (0%)]	Loss: 0.771418
Train Epoch: 4 [640/2540 (25%)]	Loss: 0.525401
Train Epoch: 4 [1280/2540 (50%)]	Loss: 0.629716
Train Epoch: 4 [1920/2540 (75%)]	Loss: 0.524130
Train Epoch: 5 [0/2540 (0%)]	Loss: 0.566314
Train Epoch: 5 [640/2540 (25%)]	Loss: 0.775011
Train Epoch: 5 [1280/2540 (50%)]	Loss: 0.729291
Train Epoch: 5 [1920/2540 (

c:\Users\micha\anaconda3\Lib\site-packages\torch\nn\_reduction.py:42: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))



Test set: Avg. loss: 1.1192, Accuracy: 6292/10000 (63%)

Round 3/8
Training client 1
Train Epoch: 1 [0/2540 (0%)]	Loss: 0.517864
Train Epoch: 1 [640/2540 (25%)]	Loss: 0.449984
Train Epoch: 1 [1280/2540 (50%)]	Loss: 0.415935
Train Epoch: 1 [1920/2540 (75%)]	Loss: 0.481164
Train Epoch: 2 [0/2540 (0%)]	Loss: 0.441029
Train Epoch: 2 [640/2540 (25%)]	Loss: 0.468470
Train Epoch: 2 [1280/2540 (50%)]	Loss: 0.548960
Train Epoch: 2 [1920/2540 (75%)]	Loss: 0.315868
Train Epoch: 3 [0/2540 (0%)]	Loss: 0.434677
Train Epoch: 3 [640/2540 (25%)]	Loss: 0.600821
Train Epoch: 3 [1280/2540 (50%)]	Loss: 0.533607
Train Epoch: 3 [1920/2540 (75%)]	Loss: 0.447099
Train Epoch: 4 [0/2540 (0%)]	Loss: 0.346863
Train Epoch: 4 [640/2540 (25%)]	Loss: 0.380581
Train Epoch: 4 [1280/2540 (50%)]	Loss: 0.257410
Train Epoch: 4 [1920/2540 (75%)]	Loss: 0.375023
Train Epoch: 5 [0/2540 (0%)]	Loss: 0.228978
Train Epoch: 5 [640/2540 (25%)]	Loss: 0.345704
Train Epoch: 5 [1280/2540 (50%)]	Loss: 0.263614
Train Epoch: 5 [1920/2540 (

...


Test set: Avg. loss: 0.8054, Accuracy: 8596/10000 (86%)

Round 7/8
Training client 1
Train Epoch: 1 [0/2540 (0%)]	Loss: 0.006608
Train Epoch: 1 [640/2540 (25%)]	Loss: 0.001302
Train Epoch: 1 [1280/2540 (50%)]	Loss: 0.003746
Train Epoch: 1 [1920/2540 (75%)]	Loss: 0.002677
Train Epoch: 2 [0/2540 (0%)]	Loss: 0.001430
Train Epoch: 2 [640/2540 (25%)]	Loss: 0.005082
Train Epoch: 2 [1280/2540 (50%)]	Loss: 0.006034
Train Epoch: 2 [1920/2540 (75%)]	Loss: 0.008171
Train Epoch: 3 [0/2540 (0%)]	Loss: 0.000824
Train Epoch: 3 [640/2540 (25%)]	Loss: 0.003521
Train Epoch: 3 [1280/2540 (50%)]	Loss: 0.003443
Train Epoch: 3 [1920/2540 (75%)]	Loss: 0.003356
Train Epoch: 4 [0/2540 (0%)]	Loss: 0.001823
Train Epoch: 4 [640/2540 (25%)]	Loss: 0.001868
Train Epoch: 4 [1280/2540 (50%)]	Loss: 0.001129
Train Epoch: 4 [1920/2540 (75%)]	Loss: 0.001776
Train Epoch: 5 [0/2540 (0%)]	Loss: 0.001966
Train Epoch: 5 [640/2540 (25%)]	Loss: 0.000876
Train Epoch: 5 [1280/2540 (50%)]	Loss: 0.000921
Train Epoch: 5 [1920/2540 (

c:\Users\micha\anaconda3\Lib\site-packages\torch\nn\_reduction.py:42: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))



Test set: Avg. loss: 0.8080, Accuracy: 8591/10000 (86%)

Round 8/8
Training client 1
Train Epoch: 1 [0/2540 (0%)]	Loss: 0.049493
Train Epoch: 1 [640/2540 (25%)]	Loss: 0.006387
Train Epoch: 1 [1280/2540 (50%)]	Loss: 0.011064
Train Epoch: 1 [1920/2540 (75%)]	Loss: 0.006899
Train Epoch: 2 [0/2540 (0%)]	Loss: 0.002672
Train Epoch: 2 [640/2540 (25%)]	Loss: 0.004002
Train Epoch: 2 [1280/2540 (50%)]	Loss: 0.000746
Train Epoch: 2 [1920/2540 (75%)]	Loss: 0.002742
Train Epoch: 3 [0/2540 (0%)]	Loss: 0.000539
Train Epoch: 3 [640/2540 (25%)]	Loss: 0.000538
Train Epoch: 3 [1280/2540 (50%)]	Loss: 0.003886
Train Epoch: 3 [1920/2540 (75%)]	Loss: 0.005205
Train Epoch: 4 [0/2540 (0%)]	Loss: 0.003133
Train Epoch: 4 [640/2540 (25%)]	Loss: 0.000820
Train Epoch: 4 [1280/2540 (50%)]	Loss: 0.001108
Train Epoch: 4 [1920/2540 (75%)]	Loss: 0.002708
Train Epoch: 5 [0/2540 (0%)]	Loss: 0.001421
Train Epoch: 5 [640/2540 (25%)]	Loss: 0.002814
Train Epoch: 5 [1280/2540 (50%)]	Loss: 0.001023
Train Epoch: 5 [1920/2540 (

c:\Users\micha\anaconda3\Lib\site-packages\torch\nn\_reduction.py:42: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))



Test set: Avg. loss: 0.8095, Accuracy: 8592/10000 (86%)



In [ ]:
print("Final Results (Non-Clustered):", results)
print("Final Results (Clustered):", clusteredResults)

# Plot

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

#TODO: we have to multiply time by 8 first

# Function to compute final metrics
def compute_final_metrics(metrics):
    final_loss = {alpha: data['losses'][-1] for alpha, data in metrics.items()}
    final_accuracy = {alpha: data['accuracy'][-1] for alpha, data in metrics.items()}
    final_precision = {alpha: data['precision'][-1] for alpha, data in metrics.items()}
    final_f1 = {alpha: data['f1'][-1] for alpha, data in metrics.items()}
    final_recall = {alpha: data['recall'][-1] for alpha, data in metrics.items()}

    # Sum of all training times
    total_time = {
        alpha: sum(data.get('TrainingTime', data.get('trainingTime', [0])))
        for alpha, data in metrics.items()
    }

    return final_loss, final_accuracy, final_precision, final_f1, final_recall, total_time

# Function to print results
def print_results(results, title):
    print(f"\n{title}:")
    for method in results.keys():
        final_loss, final_accuracy, final_precision, final_f1, final_recall, total_time = compute_final_metrics(results[method])
        print(f"{method}:")
        print("  Final Loss:", final_loss)
        print("  Final Accuracy:", final_accuracy)
        print("  Final Precision:", final_precision)
        print("  Final F1 Score:", final_f1)
        print("  Final Recall:", final_recall)
        print("  Total Time:", total_time)

# Function to plot the results
def plot_results(results, title, filename):
    plt.figure(figsize=(15, 10))

    # List of metrics to plot
    metrics_names = ["Loss", "Accuracy", "Precision", "F1 Score", "Recall", "Total Time"]
    for i, metric in enumerate(metrics_names):
        plt.subplot(2, 3, i + 1)

        # Plotting each method's metrics
        for method in results.keys():
            final_loss, final_accuracy, final_precision, final_f1, final_recall, total_time = compute_final_metrics(results[method])

            # Select the right metric based on the iteration
            metric_values = {
                "Loss": final_loss,
                "Accuracy": final_accuracy,
                "Precision": final_precision,
                "F1 Score": final_f1,
                "Recall": final_recall,
                "Total Time": total_time
            }[metric]

            # Plot the metric values for each method
            plt.plot(list(metric_values.keys()) + ['NoCluster'], list(metric_values.values()) + [metric_values.get('NoCluster', np.nan)], marker='o', label=method)

        plt.xlabel('Clusters')
        plt.ylabel(metric)
        plt.title(f'{title} - Clusters vs {metric}')
        plt.legend()

    # Adjust layout and save the plot
    plt.tight_layout()
    plt.savefig(filename)
    plt.show()

# Assuming 'results' and 'clusteredResults' are the data for the methods
# Print and plot results for non-clustered and clustered data

print_results(results, "Non-Clustered Results")
plot_results(results, "Non-Clustered Results", "non_clustered_results.png")

print_results(clusteredResults, "Clustered Results")
plot_results(clusteredResults, "Clustered Results", "clustered_results.png")
